# Тематическое моделирование

Задача тематического моделирования состоит в том, чтобы разложить слова, употребляющиеся в корпусе на темы и приписать эти темы каждому документу в корпусе.

Помимо анализа тематического наполнения корпуса, мематическое моделирование может использоваться для:

1) построения вектроных представлений текстов (числа показывают насколько тема выражена в тексте). Такие представления могут быть лучше обычных (TfidfVectorizer, CountVectorizer), т.к. позволяют находить близкие документы даже если в них нет одинаковых слов (но есть слова одной тематики). Тематические векторы могут использоваться для поиска, рекомендаций или как признаки в классификации. 

2) приписывания тэгов текстам. Так можно автоматически выделять в текстовых потоках тренды, горячие темы. Тэги можно использовать как фильтр в поисковых системах. Тэги нужно приписывать темам вручную, но это проще чем размечать обучающую выборку, так как слова в тематике сразу подказывают название. 

3) составления тематических словарей



Кроме обычных текстов тематическое моделирование применяется к многим другим данным: запросам пользователей, сайтам, на которые заходят пользователи, музыке, которую слушают пользователи, покупкам в одной корзине, банковским транзакциям и даже днк. 


Все подходы к тематическому моделированию так или иначе основнованы на:

1) модели мешка слов (т.е. порядок слов в документах не учитывается)  
2) независимости документов между собой  (т.е. употребление слова W в тексте D_1 никак не влияет на слова в документе D_2)  
3) дистрибутивной гипотезе (слова, употребляющиеся вместе, объединяются в темы)



В этой тетрадке для получения тематических моделей используются LDA из gensim и NMF из sklearn.

Про LDA (и в целом тематическое моделирование) можно почитать вот эту статью - https://sysblok.ru/knowhow/kak-ponjat-o-chem-tekst-ne-chitaja-ego/

In [1]:
import gensim
import json
import re
import pandas as pd
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from pymorphy2 import MorphAnalyzer
import pyLDAvis.gensim
import string
from collections import Counter
import warnings
warnings.filterwarnings("ignore")

morph = MorphAnalyzer()

## Данные

Возьмем 4 тыс статьи с Хабра. Это мало для хорошей тематической модели, но иначе у нас просто ничего не обучится за семинар.

В текстах есть тэги. Потрем их. Ещё токенизируем самым простым способом и нормализуем Pymorphy.

In [2]:
stops = set(stopwords.words('russian')) | {'gt',}
def remove_tags(text):
    return re.sub(r'<[^>]+>', '', text)

# чтобы быстрее нормализовать тексты, создадим словарь всех словоформ
# нормазуем каждую 1 раз и положим в словарь
# затем пройдем по текстам и сопоставим каждой словоформе её нормальную форму

def opt_normalize(texts, top=None):
    uniq = Counter()
    for text in texts:
        uniq.update(text)
    
    norm_uniq = {word:morph.parse(word)[0].normal_form for word, _ in uniq.most_common(top)}
    
    norm_texts = []
    for text in texts:
        
        norm_words = [norm_uniq.get(word) for word in text]
        norm_words = [word for word in norm_words if word and word not in stops]
        norm_texts.append(norm_words)
        
    return norm_texts

def tokenize(text):
    words = [word.strip(string.punctuation) for word in text.split()]
    words = [word for word in words if word]
    
    return words

In [4]:
texts = open('habr_texts.txt').read().splitlines()
texts = opt_normalize([tokenize(remove_tags(text.lower())) for text in texts], 30000)

In [6]:
#для нграммов
ph = gensim.models.Phrases(texts, scoring='npmi', threshold=0.4) # threshold можно подбирать
p = gensim.models.phrases.Phraser(ph)
ngrammed_texts = p[texts]

### Тематическое моделирование в gensim

Для моделей нужно сделать словарь.

In [7]:
dictinary = gensim.corpora.Dictionary(texts)

In [8]:
dictinary.filter_extremes(no_above=0.1, no_below=20)
dictinary.compactify()

In [9]:
print(dictinary)

Dictionary(6846 unique tokens: ['2-х', '3.0', 'address', 'architecture', 'assembly']...)


Преобразуем наши тексты в мешки слов. 

In [10]:
corpus = [dictinary.doc2bow(text) for text in texts]

Про параметры можно почитать в документации:

In [11]:
?gensim.models.LdaMulticore

Основные это num_topics, alpha, eta и passes. 

**num_topics** - это количество тем. Это основной параметр и настраивать его проще всего. Обычно 200 оптимальное значение. Можно поставить поменьше, если тексты не очень разнообразные или хочется уменьшить время обучения.

**alpha** и **eta** - параметры, которые влияют на разреженность распределения документы-темы и темы-слова. У alpha есть значения "asymmetric" и "auto", которые можно попробовать (по умолчанию стоит "symmetric", т.е. не разреженное). Eta можно задать каким-то числом или самому сделать изначальное распределение слов по темам. НО настраивать эти параметры сложно и непонятно и вообще лучше надеяться, что по умолчанию все заработает.

**passes** - задает количество проходов по данным. Чем больше, тем лучше сойдется модель, но обучаться будет дольше.

In [25]:
lda = gensim.models.LdaMulticore(corpus, 100, id2word=dictinary, eval_every=0, passes=10)

Посмотрим на топики.

In [22]:
lda.show_topics()

[(87,
  '0.009*"public" + 0.007*"null" + 0.005*"from" + 0.005*"as" + 0.004*"int" + 0.004*"intel" + 0.004*"set" + 0.004*"end" + 0.003*"раздел" + 0.003*"else"'),
 (44,
  '0.013*"камера" + 0.004*"плагин" + 0.004*"смартфон" + 0.003*"сигнал" + 0.003*"напряжение" + 0.003*"зона" + 0.003*"питание" + 0.002*"public" + 0.002*"шлюз" + 0.002*"частота"'),
 (107,
  '0.005*"игрок" + 0.004*"спутник" + 0.003*"php" + 0.003*"public" + 0.003*"lt" + 0.003*"боль" + 0.003*"доллар" + 0.002*"val" + 0.002*"протокол" + 0.002*"javascript"'),
 (196,
  '0.007*"null" + 0.006*"int" + 0.006*"lt" + 0.006*"n" + 0.005*"public" + 0.004*"b" + 0.004*"void" + 0.004*"end" + 0.003*"массив" + 0.003*"begin"'),
 (89,
  '0.005*"university" + 0.004*"on" + 0.003*"value" + 0.003*"int" + 0.003*"b" + 0.003*"cs" + 0.003*"вм" + 0.003*"linux" + 0.003*"•" + 0.002*"systems"'),
 (58,
  '0.005*"amp;&amp" + 0.004*"офис" + 0.003*"звук" + 0.003*"end" + 0.003*"наушник" + 0.003*"локализация" + 0.002*"менеджер" + 0.002*"буфер" + 0.002*"is" + 0.002*"

Ещё есть штука для визуализации.

In [26]:
pyLDAvis.enable_notebook()

In [27]:
pyLDAvis.gensim.prepare(lda, corpus, dictinary)

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
27    -0.164293  0.082028       1        1  5.531976
36    -0.136088 -0.019272       2        1  3.437861
29    -0.151760 -0.082568       3        1  3.368890
67    -0.089086  0.061710       4        1  3.239692
20     0.285659 -0.017598       5        1  2.368211
53     0.122573  0.020145       6        1  2.118216
44    -0.092688 -0.025138       7        1  2.106719
0     -0.165766 -0.132386       8        1  1.876848
45    -0.150999  0.018507       9        1  1.873160
49     0.170164  0.109565      10        1  1.842459
98    -0.160756 -0.088011      11        1  1.820429
17     0.270040  0.000167      12        1  1.763136
23     0.240128 -0.055508      13        1  1.757104
74    -0.085166 -0.139160      14        1  1.732413
40     0.176322  0.042837      15        1  1.706404
79    -0.046527  0.048557      16        1  1.627251
65     0.040834 -0.036048      17        1  1.448213
47    -0.131646  0.097492      18        1  1.378211
38    -0.127660  0.084240      19        1  1.359966
61     0.005011 -0.141267      20        1  1.325966
32    -0.135654 -0.028243      21        1  1.284496
35    -0.167467 -0.017251      22        1  1.248649
55     0.163463 -0.086468      23        1  1.246631
60    -0.139693  0.014411      24        1  1.229169
4      0.030312  0.094321      25        1  1.218683
91    -0.095630 -0.072958      26        1  1.176063
87     0.291774 -0.032026      27        1  1.175317
22    -0.166033 -0.111389      28        1  1.094034
56     0.183149  0.005702      29        1  1.092838
86    -0.158586 -0.059408      30        1  1.061278
...         ...       ...     ...      ...       ...
10    -0.101310  0.016442      71        1  0.573705
50    -0.083646 -0.123767      72        1  0.572464
6     -0.083662 -0.073681      73        1  0.562942
41    -0.006689  0.047294      74        1  0.555099
42     0.006497  0.090845      75        1  0.534317
80     0.142586 -0.031813      76        1  0.532864
18    -0.066912  0.030386      77        1  0.529554
16     0.058619  0.038336      78        1  0.518712
28     0.118439  0.001779      79        1  0.515872
92    -0.018360 -0.029388      80        1  0.471234
85    -0.057814  0.064670      81        1  0.460131
97    -0.010098  0.006990      82        1  0.457036
15     0.031739 -0.071455      83        1  0.449182
93    -0.027180 -0.051974      84        1  0.431260
52    -0.062236  0.024758      85        1  0.422085
46     0.050710  0.061193      86        1  0.408813
66     0.161155 -0.008097      87        1  0.405405
43     0.077287 -0.108203      88        1  0.393238
37     0.017895  0.000326      89        1  0.378523
72    -0.025073 -0.000682      90        1  0.378164
7      0.083918  0.021130      91        1  0.378077
62     0.117848 -0.015069      92        1  0.377940
2     -0.055640  0.002721      93        1  0.367300
25     0.018101  0.027157      94        1  0.334481
14    -0.074860 -0.007660      95        1  0.318314
57    -0.053373  0.007604      96        1  0.294120
94    -0.004330  0.044262      97        1  0.272557
51    -0.012846  0.027780      98        1  0.242493
76    -0.004319 -0.008624      99        1  0.229513
69     0.135128 -0.017811     100        1  0.204102

[100 rows x 5 columns], topic_info=      Category         Freq        Term        Total  loglift  logprob
716    Default  2753.000000         int  2753.000000  30.0000  30.0000
177    Default  1292.000000          up  1292.000000  29.0000  29.0000
4115   Default  1520.000000           •  1520.000000  28.0000  28.0000
58     Default  1608.000000         var  1608.000000  27.0000  27.0000
39     Default  2167.000000      public  2167.000000  26.0000  26.0000
719    Default  1844.000000          lt  1844.000000  25.0000  25.0000
4045   Default  1508.000000         end  1508.000000  24.0000  24.0000
3697   Default  1745.00000

Всё ещё есть пересекающиеся темы, да и кружочки достаточно большие. Но мне уже нравятся получившиеся темы:  
1. Тема 10: Линукс  
2. Тема 29: JavaScript  
3. Тема 23: C и язык ассемблера  

На графике должно быть как можно меньше пересекающихся кружков (т.е. темы состоят из разных слов), а сами кружки не должны быть огромными (скорее всего такую тему можно разбить на несколько поменьше).

In [29]:
tfidf = gensim.models.TfidfModel(corpus, id2word=dictinary)
corpus = tfidf[corpus]

In [40]:
lda = gensim.models.LdaMulticore(corpus, 200, id2word=dictinary, eval_every=0, passes=3)
pyLDAvis.gensim.prepare(lda, corpus, dictinary)

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
66    -0.086488 -0.035668       1        1  12.972180
107   -0.117929 -0.063448       2        1  10.990141
34    -0.158703  0.037477       3        1   8.587008
116   -0.105764 -0.065508       4        1   5.746309
60    -0.056670 -0.074112       5        1   5.734552
85    -0.136822 -0.070052       6        1   3.287228
105    0.029001 -0.202319       7        1   3.265261
46    -0.073379 -0.050111       8        1   2.358262
25    -0.081075 -0.091158       9        1   2.064810
21     0.054675 -0.174782      10        1   1.765423
148   -0.110880 -0.052396      11        1   1.749140
106   -0.160535  0.008176      12        1   1.573473
38    -0.064960 -0.052809      13        1   1.408527
24     0.026018 -0.105232      14        1   1.348876
134   -0.067172 -0.029365      15        1   1.078176
147   -0.076662 -0.028113      16        1   0.925495
163   -0.094597  0.028172      17        1   0.887209
15    -0.014640 -0.054186      18        1   0.801842
180   -0.048437 -0.028398      19        1   0.788922
7      0.010093 -0.051422      20        1   0.710695
59     0.068824 -0.110375      21        1   0.652927
126   -0.069692  0.082642      22        1   0.619016
159   -0.063454  0.004791      23        1   0.609491
99     0.041024 -0.072140      24        1   0.593584
1     -0.031122 -0.076005      25        1   0.588328
57    -0.084789 -0.000309      26        1   0.519138
135    0.072266 -0.061890      27        1   0.498256
14     0.050279 -0.081488      28        1   0.485447
153   -0.076907  0.010174      29        1   0.472795
54     0.003885 -0.020328      30        1   0.469301
...         ...       ...     ...      ...        ...
8      0.020146  0.053737     171        1   0.098006
156    0.038882  0.003916     172        1   0.097647
31     0.034614  0.030559     173        1   0.097378
124    0.027856  0.017695     174        1   0.095350
58     0.018342  0.032731     175        1   0.094179
92    -0.008084  0.042869     176        1   0.093392
198    0.021215  0.012879     177        1   0.093183
29     0.006695 -0.004202     178        1   0.091106
43     0.010060  0.022825     179        1   0.090160
190   -0.008068  0.015245     180        1   0.089872
88     0.006070  0.025819     181        1   0.089376
94     0.031280  0.012784     182        1   0.089140
174    0.057259  0.006980     183        1   0.088500
74     0.011608  0.040840     184        1   0.087912
104    0.045775  0.022576     185        1   0.087388
17     0.012345  0.040839     186        1   0.086699
89     0.024406  0.027149     187        1   0.086463
142    0.005823  0.035862     188        1   0.083560
91     0.050774  0.012417     189        1   0.083247
109    0.040578  0.030558     190        1   0.082077
52     0.025828  0.020557     191        1   0.081389
131    0.022093  0.016925     192        1   0.081309
194    0.015073  0.008963     193        1   0.081171
32     0.048642  0.013664     194        1   0.079011
42     0.049893  0.030974     195        1   0.076500
80    -0.008851  0.048410     196        1   0.074070
6      0.013980 -0.000385     197        1   0.072171
72     0.031609  0.033451     198        1   0.071359
117    0.040247  0.001977     199        1   0.071267
145    0.030273  0.008469     200        1   0.071128

[200 rows x 5 columns], topic_info=      Category       Freq             Term      Total  loglift  logprob
1498   Default  28.000000              бот  28.000000  30.0000  30.0000
4115   Default  28.000000                •  28.000000  29.0000  29.0000
1791   Default  28.000000       автомобиль  28.000000  28.0000  28.0000
39     Default  29.000000           public  29.000000  27.0000  27.0000
3697   Default  29.000000            игрок  29.000000  26.0000  26.0000
1315   Default  31.000000        процессор  31.000000  25.0000  25.0000
30     Default  34.000000  

Не знаю, что сказать даже. Получается хуже, что удивительно. Если делать больше `passes`, то он просто делает темы меньше и ближе друг к другу.
Хорошо получилась космическая тема (22) и тема про Java (21). Про JS тоже получилось, но хуже чем в прошлый раз (тема 14), туда вмешался C++.

Можно посмотреть метрики.

In [80]:
import numpy as np

Перплексия показывает насколько хороше моделируется корпус. Чем ближе к нулю, тем лучше. Можно использовать, чтобы настраивать количество проходов по корпусу (когда перестало улучшаться, то можно останавливаться).

In [81]:
lda.log_perplexity(corpus[:10000])

-9.866622134788862

Ещё есть когерентность. Она числе оценивает качество тем (проверяется, что темы состоят из разных слов и что в теме есть топ тематических слов). 

In [82]:
coherence_model_lda = gensim.models.CoherenceModel(model=lda, 
                                                  texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

Чем выше, тем лучше.

In [83]:
topics = []
for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

In [84]:
coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [85]:
coherence_model_lda.get_coherence()

0.34019684624624974

Но все эти числа вспомогательны! Главные критерии качества модели: интерпретируемость и понятность тем (т.е. нужно глазами смотреть на каждую тему), а также польза для практической задачи, которую вы пытаетесь решить.

### Разложение матриц в sklearn

![NMF](nmf.png)

NMF - превращает одну матрицу NxV в произведение двух матриц NxK и KxV (произведение не точно равно изначальной матрице, но достаточно близко - чем больше K, тем точнее, но больше тратиться памяти и времени). В нашем случае N - это документы (размер корпуса), V - количество слов в словаре, а K - количество тем. 

Таким образом, взяв одну из получившихся матриц, мы получим или тематические представления документов (первая матрица - документы на темы), либо слова, разложенные по темам (вторая матрица - темы на слова).

Отличие от LDA в том, что числа в матрицах не будут вероятностями, а просто каким-то положительными числам. Чем больше, тем сильнее слово или документ связан с темой. 

(Почему и как это все работает, вы можете почитать отдельно. Для практических задач хватит умения запускать все в sklearn) 

In [41]:
from sklearn.decomposition import NMF
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
import pandas as pd

Sklearn принимает на вход строки, поэтому склеим наши списки.

In [42]:
stexts = [' '.join(text) for text in texts]

Сделаем матрицу слова-документы с помощью TfidfVectorizer

In [43]:
vectorizer = TfidfVectorizer(max_features=1000, min_df=10, max_df=0.3, ngram_range=(1,3))
X = vectorizer.fit_transform(stexts)

Разложим её.

In [52]:
# n_components - главный параметр в NMF, это количество тем. 
# Если данных много, то увеличения этого параметра сильно увеличивает время обучения
model = NMF(n_components=200)

In [53]:
model.fit(X)

NMF(alpha=0.0, beta_loss='frobenius', init=None, l1_ratio=0.0, max_iter=200,
    n_components=200, random_state=None, shuffle=False, solver='cd', tol=0.0001,
    verbose=0)

In [54]:
model.components_.shape # матрица темы на слова

(200, 1000)

In [55]:
model.transform(X).shape # матрица документы на темы

(4121, 200)

In [56]:
pd.set_option('display.max_columns', 100)
pd.set_option('display.max_rows', 100)

Вытащим словарь, по которому мы построили модель.

In [57]:
feat_names = vectorizer.get_feature_names()

Теперь посмотрим на матрицу темы-слова, отсортируем её по строкам и возьмем топ N слов, сопоставив индексы со словарём

In [58]:
top_words = model.components_.argsort()[:,:-5:-1]

for i in range(top_words.shape[0]):
    words = [feat_names[j] for j in top_words[i]]
    print(i, "  ".join(words))

0 какой то  что то  вообще  кто
1 case  val  let  return
2 игра  игровой  играть  консоль
3 настройка  раздел  конфигурация  настроить
4 устройство  производитель  передача  поддерживать
5 lt  lt lt  gt lt  for
6 дизайн  опыт  стиль  друг
7 the  to  of  and
8 public  void  private  static
9 платформа  поддержка  запуск  поддерживать
10 социальный  facebook  новость  аудитория
11 цена  стоимость  доллар  рубль
12 файл  формат  загрузка  путь
13 доклад  конференция  тема  рассказать
14 2016  2016 год  декабрь  2017
15 память  гб  объём  производительность
16 объект  менять  свойство  сравнение
17 исследование  исследователь  научный  группа
18 массив  компилятор  хранение  переменный
19 язык  программирование  java  перевод
20 слой  архитектура  признак  набор
21 дата центр  центр  дата  оборудование
22 int  for  char  void
23 if  else  return  false
24 сигнал  частота  диапазон  выход
25 вселенная  миллиард  расширение  её
26 звук  частота  читать  характеристика
27 бот  друг  facebook 

В целом, получилось неплохо. Субъективно темы выглядят более чёткими чем с `lda`. Наверно, сюда бы хорошо добавить удаление частотных слов, потому что некоторые темы явно определяются по этим словам, что довольно плохо. Ещё я бы регулркой убрал даты, потому что они есть во всех документах, но модель почему-то на основании дат придумала тему.

У разложения есть метрика, показывающая насколько хорошо восстанавливается изначальная матрица. Чем меньше, тем лучше.

In [59]:
model.reconstruction_err_

40.66008360028658

Но как и с LDA - главное это польза от модели и человеческая оценка, получаемых тем.

## Домашнее задание

Основаная задача - **построить хорошую тематическую модель с интерпретируемыми топиками с помощью LDA в gensim и NMF в sklearn**.


1) сделайте нормализацию (если pymorphy2 работает долго используйте mystem или попробуйте установить быструю версию - `pip install pymorphy2[fast]`, можно использовать какой-то другой токенизатор); 

2) добавьте нграммы (в тетрадке есть закомменченая ячейка с Phrases,  можно также попробовать другие способы построить нграммы); 

3) сделайте хороший словарь (отфильтруйте слишком частотные и редкие слова, попробуйте удалить стоп-слова); 

4) постройте несколько LDA моделей (переберите количество тем, можете поменять alpha, passes), если получаются плохие темы, поработайте дополнительно над предобработкой и словарем; 

5) для самой хорошей модели в отдельной ячейке напечатайте 3 хороших (на ваш вкус) темы;

6) между словарем и обучением модели добавьте tfidf (`gensim.models.TfidfModel(corpus, id2word=dictionary); corpus = tfidf[corpus]`);

7) повторите пункт 4 на преобразованном корпусе;

8) в отдельной ячейке опишите как изменилась модель (приведите несколько тем, которые стали лучше или хуже, или которых раньше вообще не было; можно привести значения перплексии и когерентности для обеих моделей)

9) проделайте такие же действия для NMF (образец в конце тетрадки), для построения словаря воспользуйтесь возможностями Count или Tfidf Vectorizer (попробуйте другие значение max_features, min_df, max_df, сделайте нграмы через ngram_range, если хватает памяти), попробуйте такие же количества тем

10) в отдельной ячейки напечатайте темы лучшей NMF модели, сравните их с теми, что получились в LDA.

Сохраните тетрадку с экспериментами и положите её на гитхаб, ссылку на неё укажите в форме.

**Оцениваться будут главным образом пункты 5, 8 и 10. (2, 3, 2 баллов соответственно). Чтобы заработать остальные 3 балла, нужно хотя бы немного изменить мой код на промежуточных этапах (добавить что-то, указать другие параметры и т.д). **